# Prepare Wood vessel perforation plates data from TRY for use

The Wood vessel perforation plates trait in TRY informs about the structure of the openings between vessel elements.

*If you intend to clean more than one or two traits, we recommend the use of the batch pre-processing script. Refer to the [TRY main page](try-label) for details.*

If you have questions, suggestions, spot errors, or want to contribute, get in touch with us through planthub@idiv.de.

Author: David Schellenberger Costa

## Requirements

To run the script, the following is needed:
- TRY data, available <a href="https://planthub.idiv.de/downloads/" target="_parent">here</a>
- the data.table library may need to be installed

## Code

In [ ]:
# load in libraries
library(data.table) # handle large datasets

# clear workspace
rm(list = ls())


Let's get the TRY data

In [ ]:
# set working directory (adapt this!)
setwd(paste0(.brd, "PlantHub"))

# read in data (adapt this!)
TRY <- fread("TRY_PlantHub.gz")

# select data of interest
TRYSubset <- TRY[TraitName == "Wood vessel perforation plates"]


To get an overview of the data, we convert values to lowercase, sort them, and show them as
a table.

In [ ]:
# extract original data strings
oriVals <- TRYSubset$OrigValueStr # oriVals == original values

# change all to lowercase to ease later classification
oriVals <- tolower(oriVals)

# get an overview over the data by summarizing values and showing them in alphabetical order
valueOverview <- table(oriVals)
valueOverview[order(valueOverview)]


Some entries are just the word "yes". This should be decoded.

In [ ]:
# decode coded entries
oriVals[TRYSubset$DatasetID == 251 & oriVals == "yes"] <-
	TRYSubset[TRYSubset$DatasetID == 251 & oriVals == "yes"]$OriglName


The most important part of the cleaning process is the definition of the search strings to look for.
We use regular expressions in some cases to be more inclusive (or exclusive).

In [ ]:
# create a vector containing the search strings to look for
searchNames <- c("vesselless", "simple", "scalariform", "mixed")


We can now search for the strings defined before and give names to the new categories.

In [ ]:
# search for the strings defined before
searchResults <- sapply(searchNames, grepl, oriVals)

# name columns of searchResults matrix like corrected searchNames
colnames(searchResults) <- searchNames


Let's have a look at the results.

In [ ]:
# show the number of matches to each category
colSums(searchResults)

# show the original entries for which no match was retrieved
sort(table(oriVals[rowSums(searchResults) < 1]))

# show the number of entries that weren't matched to any category
sum(rowSums(searchResults) < 1)

# show the number of entries that were matched to more that one category
sum(rowSums(searchResults) > 1)


As the categories defined have exclusive values, we remove ambiguous entries.

In [ ]:
searchResults[rowSums(searchResults) > 1, ] <- FALSE


We can now use the cleaned results data to create a new data vector.

In [ ]:
# use the searchResults matrix to create new value strings by concatenating all data found
newVals <- sapply(seq_len(nrow(searchResults)), function(x) {
	paste(colnames(searchResults)[searchResults[x, ]], collapse = ",")
})
newVals[newVals == ""] <- NA


Let's transfer the data into the original data frame.

In [ ]:
# integrate into TRY
TRY[TraitName == "Wood vessel perforation plates", CleanedValueStr := newVals]


We may want to rename the trait.

In [ ]:
# add classification into whole plant trait or plant part trait to trait name
TRY[TraitName == "Wood vessel perforation plates", TraitName := "Wood vessel perforation plate type"]


Let's write the data to a file.

In [ ]:
# write data
fwrite(TRY, file = paste0("TRY_processed_", Sys.Date(), ".gz"))
